# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a breakfast point. Specifically, this report will be targeted to stakeholders interested in opening a **breakfast spot** in **Berlin**, near richmond circle in Bangalore.

Since there are lots of restaurants in Berlin we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no breakfast spots in the vicinity**. We would also prefer locations **as close to richmond cirle as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing breakfast spots in the neighborhood
* number of and distance to breakfast spots in the neighborhood, if any
* distance of neighborhood from richmond circle

We decided to use regularly spaced circular grids of locations, centered around Richmond Circle center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of breakfast spots and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of  center will be obtained using **Google Maps API geocoding** of well known Richmond Town in Bangalore.

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Richmond Circle, Bangalore.

Let's first find the latitude & longitude of Richmond Circle, using specific, well known address and Google Maps geocoding API.

In [3]:
# The code was removed by Watson Studio for sharing.
# place to create data sets for neighborhood
# Richmond Circle Under Fly Over, Bengaluru, Karnataka, 

google_api_key='AIzaSefcBBchangedmqxX1a41u4forsecuritylPlVreasomnsGs'

In [4]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Richmond Circle Under Fly Over, Bengaluru, Karnataka'
richmond_circle = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, richmond_circle))

Coordinate of Richmond Circle Under Fly Over, Bengaluru, Karnataka: [12.9644176, 77.5968593]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~3km from Richmond Circle. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart. Reason of chosing 3 km vicinity was because of the limit on calls that can be made to FourSquare API for number of generated neighborhoods.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [5]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Richmond Circle longitude={}, latitude={}'.format(richmond_circle[1], richmond_circle[0]))
x, y = lonlat_to_xy(richmond_circle[1], richmond_circle[0])
print('Richmond Circle UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Richmond Circle longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Richmond Circle longitude=77.5968593, latitude=12.9644176
Richmond Circle UTM X=8889780.034270031, Y=2965060.0774481003
Richmond Circle longitude=77.59685929994781, latitude=12.964417600002193


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [22]:
richmond_circle_x, richmond_circle_y = lonlat_to_xy(richmond_circle[1], richmond_circle[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = richmond_circle_x - 3000
x_step = 600
y_min = richmond_circle_y - 3000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(richmond_circle_x, richmond_circle_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

244 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [9]:
#!pip install folium

import folium

In [74]:
map_richmond = folium.Map(location=richmond_circle, zoom_start=13)
folium.Marker(richmond_circle, popup='Richmond Circle').add_to(map_richmond)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_richmond)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_richmond

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~3km from Richmond Circle. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [7]:

def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, richmond_circle[0], richmond_circle[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(richmond_circle[0], richmond_circle[1], addr))

Reverse geocoding check
-----------------------
Address of [12.9644176, 77.5968593] is: Richmond Circle (Under Fly Over), Langford Gardens, Bengaluru, Karnataka 560025, India


In [23]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', India', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [24]:
addresses[150:170]

['72/1, Shanthala Nagar, Sampangi Rama Nagar, Bengaluru, Karnataka 560001',
 '65, St Marks Rd, Shanthala Nagar, Ashok Nagar, Bengaluru, Karnataka 560001',
 'P Block, Field Marshal Cariappa Rd, Shanthala Nagar, Ashok Nagar, Bengaluru, Karnataka 560025',
 '74, Sumero Towers, Brigade Rd, Ashok Nagar, Richmond Town, Opp St Patricks, Bengaluru, Karnataka 560025',
 '27, Anthony Nicholas St, Ashok Nagar, Bengaluru, Karnataka 560025',
 '204 Raheja Plaza, 17, Commissariat Rd, Bengaluru, 560025',
 '11, M.G. Rd, Corporation Quarters, Victoria Layout, Bengaluru, Karnataka 560001',
 '95, 1st Cross Rd, Victoria Layout, Bengaluru, Karnataka 560047',
 'Lower Agaram Road, Victoria Layout, Agram, Bengaluru, Karnataka 560007',
 'Unnamed Road, Nagashettyhalli, Agram, Bengaluru, Karnataka 560007',
 '106, 1st Floor, Vikasa Soudha, Dr Ambedkar Veedhi, Bengaluru, Karnataka 560001',
 'Vidhana Soudha, Ambedkar Veedhi, Sampangi Rama Nagar, Bengaluru, Karnataka 560001',
 'High Court of Karnataka, Ambedkar Veedhi,

Looking good. Let's now place all this into a Pandas dataframe.

In [25]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  76, Journalist Colony, Kalasipalya, Bengaluru,...  12.955985  77.579510   
1  47, Lalbagh Fort Rd, Doddamavalli, Sudhama Nag...  12.954895  77.582033   
2  CS-Lalbagh Main Gate, Lalbagh Fort Rd, Doddama...  12.953805  77.584556   
3  Al-ameen towers, Hosur Main Road, Sudhama Naga...  12.952715  77.587079   
4  38, Hosur Main Road, Sudhama Nagar, Bengaluru,...  12.951624  77.589602   
5  12, Hosur Main Road, Mavalli, Bengaluru, Karna...  12.950534  77.592124   
6  50, Vinayaka Nagar, Wilson Garden, Bengaluru, ...  12.949444  77.594646   
7  88, 10th Cross Rd, Chinnayanpalya, Wilson Gard...  12.948354  77.597168   
8  122/A, 14th Cross Rd, Opp Harilakhmi Talkies, ...  12.947264  77.599689   
9  302, 7th Main Rd, Lakkasandra, Chinnayanpalya,...  12.946174  77.602211   

              X             Y  Distance from center  
0  8.887080e+06  2.961825e+06           4213.988913  
1  8.887680e+06  2.961825e+06           3857.162501  
2  8.888280e+06  2.961825e+06           3566.188800  
3  8.888880e+06  2.961825e+06           3358.229080  
4  8.889480e+06  2.961825e+06           3249.261848  
5  8.890080e+06  2.961825e+06           3249.261848  
6  8.890680e+06  2.961825e+06           3358.229080  
7  8.891280e+06  2.961825e+06           3566.188800  
8  8.891880e+06  2.961825e+06           3857.162501  
9  8.892480e+06  2.961825e+06           4213.988913

...and let's now save/persist this data into local file.

In [26]:
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'nightlife' category, 'shop and services' category and 'breakfast spot' category. So we will include in out list only venues that have these in category name. Finding out the number os spots for all these mentioned categories will help in instilling more confidence in stakeholders regarding the choice of business they want to start with.

Foursquare credentials are defined in hidden cell bellow.

In [27]:
# The code was removed by Watson Studio for sharing.
foursquare_client_id, foursquare_client_secret='154JNGBAO4somethingS15NUS5HchangedCTHORGJMWKOF','3B0JXThisCLFKNZGGME4MalsoZCA0changed2LST3KCKKC'

In [28]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', India', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [19]:
# Try getting venues as any one category to test the get_venues_near_any_location function
venues = get_venues_near_location(richmond_circle[0], richmond_circle[1], '4bf58dd8d48988d143941735', foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
len(venues)

21

In [30]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle


def get_venues(lats, lons, category_id):
    allvenues={}
    location_venues=[]
    
    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, category_id, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_venues = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            #is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            
            #if is_res:
            x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
            venue_detail = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, x, y)
            if venue_distance<=300:
                area_venues.append(venue_detail)
                
            allvenues[venue_id] = venue_detail
                
        location_venues.append(area_venues)
        
        print(' .', end='')
    print(' done.')
    
    return allvenues, location_venues

# Try to load from local file system in case we did this before

night_life_category='4d4b7105d754a06376d81259'
night_life_venues={}
location_night_lives=[]
night_life_file_name='night_life.pkl'

shop_n_service_category='4d4b7105d754a06378d81259'
shop_n_service_venues={}
location_shop_n_service=[]
shop_n_service_file_name='shop_n_service.pkl'

breakfast_spot_category='4bf58dd8d48988d143941735'
breakfast_spots={}
location_breakfast_stops=[]
breakfast_spot_file_name='breakfast_spot.pkl'


venue_categories=[night_life_file_name, shop_n_service_file_name, breakfast_spot_file_name]

for venue_category in venue_categories:

    loaded = False
    
    if 'night_life' in venue_category:
        
        try:

            with open(night_life_file_name, 'rb') as f:
                night_life_venues = pickle.load(f)
            
            with open('location_'+night_life_file_name, 'rb') as f:
                location_night_lives = pickle.load(f)
                
            print('Nightlife spots data loaded.')
            loaded = True
        except:
            pass

        # If load failed use the Foursquare API to get the data
        if not loaded:
            night_life_venues, location_night_lives = get_venues(latitudes, longitudes, night_life_category)

            # Let's persists this in local file system
            with open(night_life_file_name, 'wb') as f:
                pickle.dump(night_life_venues, f)
            
            with open('location_'+night_life_file_name, 'wb') as f:
                pickle.dump(location_night_lives, f)
                
            print('Nightlife spots data obtained.')
                
    elif 'shop_n_service' in venue_category:
        
        try:

            with open(shop_n_service_file_name, 'rb') as f:
                shop_n_service_venues = pickle.load(f)
            
            with open('location_'+shop_n_service_file_name, 'rb') as f:
                location_shop_n_service = pickle.load(f)
                
            print('Shop and Service spots data loaded.')
            loaded = True
        except:
            pass

        # If load failed use the Foursquare API to get the data
        if not loaded:
            shop_n_service_venues, location_shop_n_service = get_venues(latitudes, longitudes, shop_n_service_category)

            # Let's persists this in local file system
            with open(shop_n_service_file_name, 'wb') as f:
                pickle.dump(shop_n_service_venues, f)
            
            with open('location_'+shop_n_service_file_name, 'wb') as f:
                pickle.dump(shop_n_service_venues, f)
            
            print('Shop and Service spots data obtained.')
                
    elif 'breakfast_spot' in venue_category:
        
        try:

            with open(breakfast_spot_file_name, 'rb') as f:
                breakfast_spots = pickle.load(f)
            
            with open('location_'+breakfast_spot_file_name, 'rb') as f:
                location_breakfast_stops = pickle.load(f)
                
            print('Breakfast spots data loaded.')
            loaded = True
        except:
            pass

        # If load failed use the Foursquare API to get the data
        if not loaded:
            breakfast_spots, location_breakfast_stops = get_venues(latitudes, longitudes, breakfast_spot_category)

            # Let's persists this in local file system
            with open(breakfast_spot_file_name, 'wb') as f:
                pickle.dump(breakfast_spots, f)
            
            with open('location_'+night_life_file_name, 'wb') as f:
                pickle.dump(location_breakfast_stops, f)
            
            print('Breakfast spots data obtained.')

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.
Nightlife spots data obtained.
Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .

In [31]:
import numpy as np

print('Total number of Night Life spots:', len(night_life_venues))
print('Average number of night life spots in neighborhood:', np.array([len(r) for r in location_night_lives]).mean())

print('Total number of Shop and Service venues:', len(shop_n_service_venues))
print('Average number of  Shop and Service venues in neighborhood:', np.array([len(r) for r in location_shop_n_service]).mean())

print('Total number of breakfast spots:', len(breakfast_spots))
print('Average number of breakfast spots in neighborhood:', np.array([len(r) for r in location_breakfast_stops]).mean())


Total number of Night Life spots: 126
Average number of night life spots in neighborhood: 1.5327868852459017
Total number of Shop and Service venues: 575
Average number of  Shop and Service venues in neighborhood: 6.19672131147541
Total number of breakfast spots: 237
Average number of breakfast spots in neighborhood: 3.040983606557377


In [35]:
print('-----------------------')
print('List of all night life spots')
print('-----------------------')
for r in list(night_life_venues.values())[:10]:
    print(r)
print('...')
print('Total:', len(night_life_venues))

print('-----------------------')
print('List of all shop n service  spots')
print('-----------------------')
for r in list(shop_n_service_venues.values())[:10]:
    print(r)
print('...')
print('Total:', len(shop_n_service_venues))

print('-----------------------')
print('List of all breakfast spots')
print('-----------------------')
for r in list(breakfast_spots.values())[:10]:
    print(r)
print('...')
print('Total:', len(breakfast_spots))



-----------------------
List of all night life spots
-----------------------
('4c6d573b46353704a7c108bc', 'Upper Deck', 12.956464343758645, 77.58047295589992, 'Pai Viceroy, JC Road, Bangalore, Karnātaka', 185, 8887228.903905662, 2962006.407890346)
('50ade477e4b05090c0d41a59', 'Costarica bar', 12.954587112670714, 77.5796814750655, 'India', 257, 8887239.22279178, 2961555.8225103826)
('586bccb49e35d309bfc5d559', 'Steaming Mugs', 12.953452, 77.580383, 'Bangalore, Karnātaka', 240, 8887480.459819702, 2961386.891416425)
('516fb513d86c1212c3ab08b8', 'Beetle Juice Bar', 12.95649237204395, 77.58352875709534, 'No. 19, H-siddiah Road, Bengaluru - 560 027. (Opposite Lions eye hospital), Bangalore 560002, Karnātaka', 302, 8887834.914104737, 2962280.2489024573)
('5780158c498e010ca9aede58', 'Wilson Garden Club', 12.947919, 77.59464, 'Wilson Garden,, Bangalore 560027, Karnātaka', 278, 8890815.39193308, 2961514.372607275)
('4e82d2e7f5b9796ec72c3930', 'MAY FLOWER The Business Hotel', 12.948275956165299, 

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

So now we have all the restaurants in area within few kilometers from Richmond Circle, and we know their number! We also know which breakfast points exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a breakfast spot/point near Richmond Circle.

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Bengalure that have low breakfast spot density. We will limit our analysis to area ~3km around richmod circle.

In first step we have collected the required **data: location and type (category) of every restaurant within 3km from Richmond Circle** (Under the Fly Over). We have also **identified breakfast spots** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**breakfast spot density**' across different areas of Bengaluru - we will use **heatmaps** to identify a few promising areas close to center with low number of breakfast spot in general (*and* less breakfast spot in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two breakfast spot in radius of 250 meters**, and we want locations **without breakfast spot in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of breakfast spot, night life spots and shop and services spots in every area candidate**:

In [33]:
location_night_lives_count = [len(res) for res in location_night_lives]
location_shop_n_service_count = [len(res) for res in location_shop_n_service]
location_breakfast_stops_count = [len(res) for res in location_breakfast_stops]

df_locations['Night_Life_Spots_In_Area'] = location_night_lives_count
df_locations['Shop_N_Service_Spots_In_Area'] = location_shop_n_service_count
df_locations['Breakfast_Spots_In_Area'] = location_breakfast_stops_count

print('Average number of Night Life spots in every area with radius=300m:', np.array(location_night_lives_count).mean())
print('Average number of Shop and Service spots in every area with radius=300m:', np.array(location_shop_n_service_count).mean())
print('Average number of Breakfast spots in every area with radius=300m:', np.array(location_breakfast_stops_count).mean())

df_locations.head(10)

Average number of Night Life spots in every area with radius=300m: 1.5327868852459017
Average number of Shop and Service spots in every area with radius=300m: 6.19672131147541
Average number of Breakfast spots in every area with radius=300m: 3.040983606557377


Address   Latitude  Longitude  \
0  76, Journalist Colony, Kalasipalya, Bengaluru,...  12.955985  77.579510   
1  47, Lalbagh Fort Rd, Doddamavalli, Sudhama Nag...  12.954895  77.582033   
2  CS-Lalbagh Main Gate, Lalbagh Fort Rd, Doddama...  12.953805  77.584556   
3  Al-ameen towers, Hosur Main Road, Sudhama Naga...  12.952715  77.587079   
4  38, Hosur Main Road, Sudhama Nagar, Bengaluru,...  12.951624  77.589602   
5  12, Hosur Main Road, Mavalli, Bengaluru, Karna...  12.950534  77.592124   
6  50, Vinayaka Nagar, Wilson Garden, Bengaluru, ...  12.949444  77.594646   
7  88, 10th Cross Rd, Chinnayanpalya, Wilson Gard...  12.948354  77.597168   
8  122/A, 14th Cross Rd, Opp Harilakhmi Talkies, ...  12.947264  77.599689   
9  302, 7th Main Rd, Lakkasandra, Chinnayanpalya,...  12.946174  77.602211   

              X             Y  Distance from center  Night_Life_Spots_In_Area  \
0  8.887080e+06  2.961825e+06           4213.988913                         3   
1  8.887680e+06  2.961825e+06           3857.162501                         4   
2  8.888280e+06  2.961825e+06           3566.188800                         0   
3  8.888880e+06  2.961825e+06           3358.229080                         0   
4  8.889480e+06  2.961825e+06           3249.261848                         0   
5  8.890080e+06  2.961825e+06           3249.261848                         0   
6  8.890680e+06  2.961825e+06           3358.229080                         1   
7  8.891280e+06  2.961825e+06           3566.188800                         3   
8  8.891880e+06  2.961825e+06           3857.162501                         2   
9  8.892480e+06  2.961825e+06           4213.988913                         0   

   Shop_N_Service_Spots_In_Area  Breakfast_Spots_In_Area  
0                             3                        3  
1                             2                        4  
2                             4                        1  
3                             2                        0  
4                             3                        0  
5                             4                        2  
6                            10                        3  
7                            13                        5  
8                             7                        5  
9                             1                        0

OK, now let's calculate the **distance to nearest breakfast spot from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [39]:
distances_to_breakfast_spots= []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in breakfast_spots.values():
        res_x = res[6]
        res_y = res[7]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_breakfast_spots.append(min_distance)

df_locations['Distance_to_Breakfast_spots'] = distances_to_breakfast_spots

In [40]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  76, Journalist Colony, Kalasipalya, Bengaluru,...  12.955985  77.579510   
1  47, Lalbagh Fort Rd, Doddamavalli, Sudhama Nag...  12.954895  77.582033   
2  CS-Lalbagh Main Gate, Lalbagh Fort Rd, Doddama...  12.953805  77.584556   
3  Al-ameen towers, Hosur Main Road, Sudhama Naga...  12.952715  77.587079   
4  38, Hosur Main Road, Sudhama Nagar, Bengaluru,...  12.951624  77.589602   
5  12, Hosur Main Road, Mavalli, Bengaluru, Karna...  12.950534  77.592124   
6  50, Vinayaka Nagar, Wilson Garden, Bengaluru, ...  12.949444  77.594646   
7  88, 10th Cross Rd, Chinnayanpalya, Wilson Gard...  12.948354  77.597168   
8  122/A, 14th Cross Rd, Opp Harilakhmi Talkies, ...  12.947264  77.599689   
9  302, 7th Main Rd, Lakkasandra, Chinnayanpalya,...  12.946174  77.602211   

              X             Y  Distance from center  Night_Life_Spots_In_Area  \
0  8.887080e+06  2.961825e+06           4213.988913                         3   
1  8.887680e+06  2.961825e+06           3857.162501                         4   
2  8.888280e+06  2.961825e+06           3566.188800                         0   
3  8.888880e+06  2.961825e+06           3358.229080                         0   
4  8.889480e+06  2.961825e+06           3249.261848                         0   
5  8.890080e+06  2.961825e+06           3249.261848                         0   
6  8.890680e+06  2.961825e+06           3358.229080                         1   
7  8.891280e+06  2.961825e+06           3566.188800                         3   
8  8.891880e+06  2.961825e+06           3857.162501                         2   
9  8.892480e+06  2.961825e+06           4213.988913                         0   

   Shop_N_Service_Spots_In_Area  Breakfast_Spots_In_Area  \
0                             3                        3   
1                             2                        4   
2                             4                        1   
3                             2                        0   
4                             3                        0   
5                             4                        2   
6                            10                        3   
7                            13                        5   
8                             7                        5   
9                             1                        0   

   Distance to Breakfast spots  Distance_to_Breakfast_spots  
0                   150.464541                   150.464541  
1                   371.990117                   371.990117  
2                   363.896433                   363.896433  
3                   629.263630                   629.263630  
4                   764.118072                   764.118072  
5                   230.791168                   230.791168  
6                   327.428327                   327.428327  
7                   150.810712                   150.810712  
8                   471.424740                   471.424740  
9                  1061.166412                  1061.166412

In [41]:
print('Average distance to closest Breakfast spot from each area center:', df_locations['Distance_to_Breakfast_spots'].mean())

Average distance to closest Breakfast spot from each area center: 569.7323627628746


OK, so **on average Breakfast spot can be found within ~600m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of breakfast spots** and try to extract some meaningfull info from that. Also, let's show **borders of Richmond boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from Richmond circle.

In [43]:
berlin_boroughs_url = 'https://raw.githubusercontent.com/stupidnetizen/Coursera_Capstone/master/richmond_circle_area.geojson'
import json
# Download from the above URL and load the geojson file
with open('richmond_circle_area.geojson', 'r') as f:
    richmond_boroughs = json.load(f)

def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [44]:
night_life_spots_latlons = [[res[2], res[3]] for res in night_life_venues.values()]

breakfast_spots_latlons = [[res[2], res[3]] for res in breakfast_spots.values()]

In [47]:
import folium
from folium import plugins
from folium.plugins import HeatMap

map_richmond = folium.Map(location=richmond_circle, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_richmond) #cartodbpositron cartodbdark_matter
HeatMap(night_life_spots_latlons).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
folium.Circle(richmond_circle, radius=1000, fill=False, color='white').add_to(map_richmond)
folium.Circle(richmond_circle, radius=2000, fill=False, color='white').add_to(map_richmond)
folium.Circle(richmond_circle, radius=3000, fill=False, color='white').add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Looks like a few pockets of low night life spots density closest to city center can be found **south, south-east and west from Richmond Circle**. 

Let's create another heatmap map showing **heatmap/density of breakfast spot** only.

In [49]:
map_richmond = folium.Map(location=richmond_circle, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_richmond) #cartodbpositron cartodbdark_matter
HeatMap(breakfast_spots_latlons).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
folium.Circle(richmond_circle, radius=1000, fill=False, color='white').add_to(map_richmond)
folium.Circle(richmond_circle, radius=2000, fill=False, color='white').add_to(map_richmond)
folium.Circle(richmond_circle, radius=3000, fill=False, color='white').add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

This map is so 'hot' (breakfast spot are quite densly distributed near RIchmond Circle) it also indicates higher density of existing breakfast spot directly north and west from Richmond Circle, with closest pockets of **low breakfast spot density positioned east, south-east and south from richmond circle**.

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from Richmond Circle center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs with large low restaurant density south and south west from richmond circle, however this borough is less interesting to stakeholders as it's mostly residental and less popular with tourists).

In [52]:
roi_x_min = richmond_circle_x - 2000
roi_y_max = richmond_circle_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_richmond = folium.Map(location=roi_center, zoom_start=14)
HeatMap(breakfast_spots_latlons).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Not bad - this nicely covers all the pockets of low breakfast spot density in nearby bouroughs.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [53]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of breakfast spot in vicinity** (we'll use radius of **250 meters**) and **distance to closest breakfast spot**.

In [54]:
def count_breakfast_spots_nearby(x, y, breakfast_spots, radius=250):    
    count = 0
    for res in breakfast_spots.values():
        res_x = res[6]; res_y = res[7]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_breakfast_spot(x, y, breakfast_spots):
    d_min = 100000
    for res in breakfast_spots.values():
        res_x = res[6]; res_y = res[7]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_breakfast_spots_counts = []
roi_breakfast_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_breakfast_spots_nearby(x, y, breakfast_spots, radius=250)
    roi_breakfast_spots_counts.append(count)
    distance = find_nearest_breakfast_spot(x, y, breakfast_spots)
    roi_breakfast_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [55]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Breakfast spots nearby':roi_breakfast_spots_counts,
                                 'Distance to breakfast spot':roi_breakfast_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Breakfast spots nearby  \
0  12.947109  77.591338  8.890230e+06  2.961060e+06                       0   
1  12.946928  77.591759  8.890330e+06  2.961060e+06                       0   
2  12.948465  77.589186  8.889680e+06  2.961147e+06                       0   
3  12.948284  77.589607  8.889780e+06  2.961147e+06                       0   
4  12.948102  77.590027  8.889880e+06  2.961147e+06                       0   
5  12.947920  77.590448  8.889980e+06  2.961147e+06                       0   
6  12.947739  77.590868  8.890080e+06  2.961147e+06                       0   
7  12.947557  77.591288  8.890180e+06  2.961147e+06                       0   
8  12.947376  77.591709  8.890280e+06  2.961147e+06                       0   
9  12.947194  77.592129  8.890380e+06  2.961147e+06                       0   

   Distance to breakfast spot  
0                  725.215738  
1                  673.141244  
2                  891.828534  
3                  824.636801  
4                  764.652584  
5                  713.695519  
6                  673.816751  
7                  647.067797  
8                  635.109797  
9                  577.749144

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two breakfast spot in radius of 250 meters**, and **no breakfast spot in radius of 400 meters**.

In [56]:
good_res_count = np.array((df_roi_locations['Breakfast spots nearby']<=2))
print('Locations with no more than two Breakfast spots nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to breakfast spot']>=400)
print('Locations with no breakfast_spot  within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two Breakfast spots nearby: 2058
Locations with no breakfast_spot  within 400m: 934
Locations with both conditions met: 934


Let's see how this looks on a map.

In [57]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_richmond = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_richmond)
HeatMap(breakfast_spots_latlons).add_to(map_richmond)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond) 
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Looking good. We now have a bunch of locations fairly close to Richmond Circle (mostly in south and south east of Richmond borough), and we know that each of those locations has no more than two restaurants in radius of 250m, and no breakfast spot closer than 400m. Any of those locations is a potential candidate for a new breakfast spot, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [58]:
map_richmond = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [72]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_richmond = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_richmond)
HeatMap(breakfast_spots_latlons).add_to(map_richmond)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_richmond)
folium.Marker(richmond_circle).add_to(map_richmond)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_richmond) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [64]:
map_richmond = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(richmond_circle).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_richmond) 
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Let's zoom in on candidate areas in **Richmond Town**:

In [66]:
map_richmond = folium.Map(location=richmond_circle, zoom_start=15)
folium.Marker(richmond_circle).add_to(map_richmond)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_richmond) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

...and candidate areas near **Richmond Circle**:

In [67]:
map_richmond = folium.Map(location=richmond_circle, zoom_start=15)
folium.Marker(richmond_circle).add_to(map_richmond)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_richmond) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_richmond)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_richmond)
folium.GeoJson(richmond_boroughs, style_function=boroughs_style, name='geojson').add_to(map_richmond)
map_richmond

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [69]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', India', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, richmond_circle_x, richmond_circle_y)
    print('{}{} => {:.1f}km from Richmond Circle'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

10/2, Alfred St, Richmond Town, Bengaluru, Karnataka 560025 => 1.8km from Richmond Circle
Hosur Main Road, Sudhama Nagar, Bengaluru, Karnataka 560004 => 3.2km from Richmond Circle
147, 2nd Main Rd, Jalakanteshwara Nagar, Shanti Nagar, Bengaluru, Karnataka 560027 => 2.6km from Richmond Circle
Laxmi Road, Shantinagar                            => 1.2km from Richmond Circle
77, SUPREM KUTIR, 5th Cross Rd, Bheemanna Garden, Ayappa Garden, Shanti Nagar, Bengaluru, Karnataka 560027 => 1.7km from Richmond Circle
9, 1st Cross Rd, K.S. Garden, Sudhama Nagar, Bengaluru, Karnataka 560027 => 2.5km from Richmond Circle
27/1, Hosur Rd, Langford Town, Shanti Nagar, Bengaluru, Karnataka 560025 => 2.9km from Richmond Circle
13, 5th Cross Rd, Sudhama Nagar, Bengaluru, Karnataka 560027 => 2.7km from Richmond Circle
16, Muniyappa Rd, Sampangi Rama Nagara, Sampangi Rama Nagar, Bengaluru, Karnataka 560027 => 0.9km from Richmond Circle
KSRTC Bus

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of breakfast spot and no breakfast spot nearby, all zones being fairly close to city center (all less than 4km from Richmond Circle, and about half of those less than 2km from Richmond circle). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located around nearby boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [71]:
map_richmond = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(richmond_circle, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_richmond)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_richmond) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_richmond)
map_richmond

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of breakfast spot in Bengaluru , there are pockets of low breakfast spot density fairly close to richmond circle center. Highest concentration of breakfast spot was detected north and east from Richmond Circle, so we focused our attention to areas south, south-west and west, corresponding to boroughs near by. 

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from Richmond Circle) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two breakfast spots in radius of 250m and those with breakfast spot closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new breakfast spot locations based on number of and distance to existing venues. This, of course, does not imply that those zones are actually optimal locations for a new breakfast spot! Purpose of this analysis was to only provide info on areas close to Richmond circle center but not crowded with existing breakfast spot - it is entirely possible that there is a very good reason for small number of breakfast spot in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Bengaluru areas close to center with low number of breakfast spot in order to aid stakeholders in narrowing down the search for optimal location for a new breakfast spot. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis , and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal breakfast spot location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.